# Coswara Audio Classification

In this notebook, we will demonstrate using a custom SagemMaker PyTorch container to train an acoustic classification model in SageMaker script mode.

In this example, the model take reference to the paper VERY DEEP CONVOLUTIONAL NEURAL NETWORKS FOR RAW WAVEFORMS by Wei Dai et al., you can get more information by reading the paper.

### Dataset

We will use the Coswara dataset to train our network. It is available for free here <https://github.com/iiscleap/Coswara-Data> The data set distribution is here <https://iiscleap.github.io/coswara-blog/coswara/2020/11/23/visualize_coswara_data_metadata.html>

The following are the class labels:
```
0 = healthy 
1 = resp_illness_not_identified
1 = no_resp_illness_exposed 
1 = recovered_full
1 = positive_mild
1 = positive_asymp 
1 = positive_moderate
```

The expected directory structure is as follows with respect to this notebook:

```
../../Coswara-Data/
|-- 20200413
|   |-- 20200413.csv
|   |-- 20200413.tar.gz.aa
|   |-- 20200413.tar.gz.ab
|   |-- 20200413.tar.gz.ac
|   |-- 20200413.tar.gz.ad
...
|   
`-- combined_data.csv
```

Let's take a look at a sample file to ensure dataset is downloaded to the correct location.

### first process the raw Coswara data
uncompress
generate metadata file for each type of recording

In [4]:
!chmod u+x ../preprocess.sh
!../preprocess.sh

Processing folder: 20200413
number of annotated samples is 77
Processing folder: 20200415
number of annotated samples is 162
Processing folder: 20200416
number of annotated samples is 198
Processing folder: 20200417
number of annotated samples is 169
Processing folder: 20200418
number of annotated samples is 47
Processing folder: 20200419
number of annotated samples is 34
Processing folder: 20200424
number of annotated samples is 29
Processing folder: 20200430
number of annotated samples is 24
Processing folder: 20200502
number of annotated samples is 156
Processing folder: 20200504
number of annotated samples is 82
Processing folder: 20200505
number of annotated samples is 15
Processing folder: 20200525
number of annotated samples is 55
Processing folder: 20200604
number of annotated samples is 21
Processing folder: 20200707
number of annotated samples is 43
Processing folder: 20200720
number of annotated samples is 22
Processing folder: 20200803
number of annotated samples is 30
Proc

In [2]:
import boto3
import sagemaker
from sagemaker import get_execution_role
from sagemaker.pytorch import PyTorch
import warnings
warnings.filterwarnings('ignore')

role = get_execution_role()
ecr_repository_name = 'coswara-audio-classification'
account_id = role.split(':')[4]
region = boto3.Session().region_name
sagemaker_session = sagemaker.Session(default_bucket='sagemaker-pytorch-audio-classification-{}'.format(account_id))
bucket = sagemaker_session.default_bucket()


print('Account: {}'.format(account_id))
print('Region: {}'.format(region))
print('Role: {}'.format(role))
print('S3 Bucket: {}'.format(bucket))

Account: 948279062543
Region: us-west-2
Role: arn:aws:iam::948279062543:role/SageMakerAPIExecutionRole
S3 Bucket: sagemaker-pytorch-audio-classification-948279062543


In [7]:
## play a sample audio recording
from IPython.display import Audio

coswarapath = '/home/ec2-user/SageMaker/Coswara-Data/20200413/20200413'
audioid = 'l3umDXECeOUTZH8pFN19c2WM4m43'
audiotype = 'breathing-deep.wav'
filename = '/'.join([coswarapath, audioid, audiotype])
Audio(filename, autoplay=False)

In [8]:
%%writefile build_and_push.sh

ACCOUNT_ID=$1
REGION=$2
REPO_NAME=$3
DOCKERFILE=$4
SERVER="${ACCOUNT_ID}.dkr.ecr.${REGION}.amazonaws.com"

echo "ACCOUNT_ID: ${ACCOUNT_ID}"
echo "REPO_NAME: ${REPO_NAME}"
echo "REGION: ${REGION}"
echo "DOCKERFILE: ${DOCKERFILE}"

# Login to retrieve base container
aws ecr get-login-password | docker login --username AWS --password-stdin 763104351884.dkr.ecr.${REGION}.amazonaws.com

docker build -q -f ${DOCKERFILE} -t ${REPO_NAME} .

docker tag ${REPO_NAME} ${ACCOUNT_ID}.dkr.ecr.${REGION}.amazonaws.com/${REPO_NAME}:latest

aws ecr get-login-password | docker login --username AWS --password-stdin ${SERVER}
aws ecr describe-repositories --repository-names ${REPO_NAME} || aws ecr create-repository --repository-name ${REPO_NAME}

docker push ${ACCOUNT_ID}.dkr.ecr.${REGION}.amazonaws.com/${REPO_NAME}:latest

Writing build_and_push.sh


In [9]:
!bash build_and_push.sh $account_id $region $ecr_repository_name Dockerfile

ACCOUNT_ID: 948279062543
REPO_NAME: coswara-audio-classification
REGION: us-west-2
DOCKERFILE: Dockerfile
WARNING! Your password will be stored unencrypted in /home/ec2-user/.docker/config.json.
Configure a credential helper to remove this warning. See
https://docs.docker.com/engine/reference/commandline/login/#credentials-store

Login Succeeded
sha256:181b7f9561a83fbda61af84a8ce2c9ee86d73e0be634f93c86a58ce81850f380
WARNING! Your password will be stored unencrypted in /home/ec2-user/.docker/config.json.
Configure a credential helper to remove this warning. See
https://docs.docker.com/engine/reference/commandline/login/#credentials-store

Login Succeeded

An error occurred (RepositoryNotFoundException) when calling the DescribeRepositories operation: The repository with name 'coswara-audio-classification' does not exist in the registry with id '948279062543'
{
    "repository": {
        "repositoryArn": "arn:aws:ecr:us-west-2:948279062543:repository/coswara-audio-classification",
     

In [ ]:
## first time run this to upload data to S3
train_data = sagemaker_session.upload_data(
    "/home/ec2-user/SageMaker/Coswara-Data/",
    bucket=bucket,
    key_prefix="Coswara-Data",
)

In [ ]:
## following run this to avoid upload
train_data = "s3://sagemaker-pytorch-audio-classification-{}/Coswara-Data".format(account_id)

train_input = sagemaker.session.TrainingInput(train_data,
                                    distribution='FullyReplicated',
                                    content_type='csv',
                                    s3_data_type='S3Prefix')

train_image_uri = '{0}.dkr.ecr.{1}.amazonaws.com/{2}:latest'.format(account_id, region, ecr_repository_name)
print('ECR training container ARN: {}'.format(train_image_uri))

hyperparams = {'lr': 0.09423, # learning rate
               'gamma': 0.31665, # Learning rate step gamma
               'weight-decay': 0.000001, # Optimizer regularization
               'stepsize': 10, # Optimizer stepsize
               'epochs': 50, # iterations to stablize
               'batch-size': 256, # train batch size
               'num-workers': 30,
               'csv-file': 'breathing-shallow-metadata.csv' ## breathing-deep-metadata.csv, cough-heavy-metadata.csv, cough-shallow-metadata.csv, counting-fast-metadata.csv, counting-normal-metadata.csv, vowel-a-metadata.csv, vowel-e-metadata.csv, vowel-o-metadata.csv
              }

pytorch_estimator = PyTorch(image_uri=train_image_uri,
                            entry_point='train.py',
                            source_dir='./',
                            role=role,
                            instance_type='ml.c4.2xlarge',
                            instance_count=1,
                            output_path = "s3://{}/".format(bucket),
                            hyperparameters = hyperparams,
                            metric_definitions=[
                                {'Name': 'train:loss', 'Regex': '011Loss: ([0-9\\.]+)'},
                                {'Name': 'test:loss', 'Regex': 'Average loss: ([0-9\\.]+)'},
                                {'Name': 'test:accuracy', 'Regex': 'Accuracy: ([0-9\\.]+)'}
                            ]
                           )


pytorch_estimator.fit({'training': train_input}, wait=True)

ECR training container ARN: 948279062543.dkr.ecr.us-west-2.amazonaws.com/coswara-audio-classification:latest
2021-01-02 20:05:32 Starting - Starting the training job...
2021-01-02 20:05:35 Starting - Launching requested ML instancesProfilerReport-1609617931: InProgress
......
2021-01-02 20:06:44 Starting - Preparing the instances for training......
2021-01-02 20:07:45 Downloading - Downloading input data...............
2021-01-02 20:10:28 Training - Downloading the training image.................
2021-01-02 20:13:29 Training - Training image download completed. Training in progress.bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-01-02 20:13:19,716 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-01-02 20:13:19,719 sagemaker-training-toolkit INFO     No GPUs detected (normal if no gpus installed)
2021-01-02 20:13:19,729 sagemaker_pytorch_container.training INFO     Block 

Namespace(batch_size=256, csv_file='breathing-shallow-metadata.csv', data_dir='/opt/ml/input/data/training', epochs=50, gamma=0.31665, localpath='data', log_interval=10, lr=0.09423, model='m3', model_dir='/opt/ml/model', num_workers=30, seed=1, stepsize=10, test_batch_size=64, weight_decay=1e-06)
Device: cpu
Running on sagemaker
csv_path /opt/ml/input/data/training/breathing-shallow-metadata.csv
file_path /opt/ml/input/data/training
{}
train_size: 1164, test_size:292
Loading model: m3
Learning rate: 0.09423
Train Epoch: 1 [0/1164 (0%)]#011Loss: 2.017374
Test set: Average loss: 2.7013, Accuracy: 238/292 (82%)
Precision: [0.81506849 0.        ]
Recall: [1. 0.]


Learning rate: 0.09423
Train Epoch: 2 [0/1164 (0%)]#011Loss: 3.815962
Test set: Average loss: 0.8996, Accuracy: 238/292 (82%)
Precision: [0.81506849 0.        ]
Recall: [1. 0.]


Learning rate: 0.09423
Train Epoch: 3 [0/1164 (0%)]#011Loss: 0.911366
Test set: Average loss: 0.6303, Accuracy: 238/292 (82%)
Precision: [0.81506849 0. 

In [3]:
model_location = pytorch_estimator.model_data
print(model_location)

s3://sagemaker-pytorch-audio-classification-948279062543/coswara-audio-classification-2021-01-02-17-25-45-116/output/model.tar.gz


In [ ]:
## hyperparameter tuning (optional to run)

objective_metric_name = 'test:accuracy'
objective_type = 'Maximize'
metric_definitions = [
    {'Name': 'train:loss', 'Regex': '011Loss: ([0-9\\.]+)'},
    {'Name': 'test:loss', 'Regex': 'Average loss: ([0-9\\.]+)'},
    {'Name': 'test:accuracy', 'Regex': 'Accuracy: ([0-9\\.]+)'}
]

hyperparameter_ranges = {
    'lr': sagemaker.tuner.ContinuousParameter(0.0001, 0.1),
    'gamma': sagemaker.tuner.ContinuousParameter(0.005, 0.5),
    'weight-decay': sagemaker.tuner.CategoricalParameter([0.000001, 0.00001, 0.001]), 
    'stepsize': sagemaker.tuner.CategoricalParameter([1,5,10])
}

tuner = sagemaker.tuner.HyperparameterTuner(pytorch_estimator,
                            objective_metric_name,
                            hyperparameter_ranges,
                            metric_definitions,
                            max_jobs=10,
                            max_parallel_jobs=2,
                            objective_type=objective_type)

tuner.fit({'training': train_input})

........................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

In [4]:
from sagemaker.pytorch import PyTorchModel

pytorch_model = PyTorchModel(model_data=model_location, 
                             role=role, 
                             entry_point='inference.py',
                             source_dir='./',
                             py_version='py3',
                             framework_version='1.6.0',
                            )
predictor = pytorch_model.deploy(initial_instance_count=1, instance_type='ml.m4.xlarge', wait=True)

---------------------!

In [5]:
pytorch_model.endpoint_name

'pytorch-inference-2021-01-02-17-59-05-357'

In [24]:
# !conda install -c conda-forge librosa -y
!pip install torchaudio
# !pip install -q pysndfile librosa==0.7.2 numba==0.48

     |████████████████████████████████| 7.6 MB 6.3 MB/s eta 0:00:01
     |█████████████████████▊          | 526.5 MB 73.4 MB/s eta 0:00:044    |▎                               | 7.7 MB 74.2 MB/s eta 0:00:11MB 93.5 MB/s eta 0:00:07

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



     |████████████████████████▋       | 598.2 MB 85.5 MB/s eta 0:00:03

     |████████████████████████▉       | 603.3 MB 85.5 MB/s eta 0:00:03

     |█████████████████████████       | 608.0 MB 85.5 MB/s eta 0:00:02

...

     |███████████████████████████████▌| 764.6 MB 76.8 MB/s eta 0:00:01

     |███████████████████████████████▊| 768.9 MB 76.8 MB/s eta 0:00:01

     |███████████████████████████████▉| 773.2 MB 76.8 MB/s eta 0:00:01

     |████████████████████████████████| 776.8 MB 76.8 MB/s eta 0:00:01

     |████████████████████████████████| 776.8 MB 11 kB/s 
  Attempting uninstall: torch
    Found existing installation: torch 1.7.0
    Uninstalling torch-1.7.0:
      Successfully uninstalled torch-1.7.0
You should consider upgrading via the '/home/ec2-user/anaconda3/envs/pytorch_latest_p36/bin/python -m pip install --upgrade pip' command.


In [6]:
from coswara_dataset import CoswareDataset
from pathlib import Path
import torch

datapath = Path("/home/ec2-user/SageMaker/Coswara-Data")
csvpath = datapath / "breathing-deep-metadata.csv"

test_set = CoswareDataset(
    csv_path=csvpath,
    file_path=datapath,
    new_sr=8000,
    audio_len=20,
    sampling_ratio=5,
)
test_loader = torch.utils.data.DataLoader(test_set, batch_size=50)

In [7]:
X, y = next(iter(test_loader))
print(X.shape, y)

torch.Size([50, 1, 32000]) tensor([0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1,
        0, 0])


In [8]:
import numpy as np
response = predictor.predict(X.numpy())
response = np.transpose(response, (1, 0, 2))
prediction = response[0].argmax(axis=1)
print(prediction)

[0 1 0 1 1 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 1 0 0 0 1 0 1
 0 1 0 0 0 0 0 0 0 0 1 0 0]


In [9]:
import boto3

client = boto3.client('sagemaker-runtime')
response = client.invoke_endpoint(
    EndpointName='pytorch-inference-2021-01-02-17-59-05-357',
    Body='s3://sagemaker-pytorch-audio-classification-{}/Coswara-Data/20200413/20200413/0Rlzhiz6bybk77wdLjxwy7yLDhg1/breathing-shallow.wav'.format(account_id),
    ContentType='text/csv',
)

In [10]:
response['Body'].read().decode("utf-8")

'[[[-0.696111798286438, -0.6905001401901245, -10.3273344039917, -10.456316947937012, -10.194159507751465, -10.560397148132324, -10.415157318115234]]]'